In [22]:
#https://www.nicksniche.net/lineup-optimization/lineup-optimizer-part-1

import pandas as pd
import numpy as np
import re as re
from pulp import *
import openpyxl
import pygolf_vectorize as pg
import pydfs_lineup_optimizer as pdfs







print('hi')



hi


In [17]:
players = pd.read_csv('PGA_Champ_PlayerList.csv',usecols=['Position','Name + ID','Name','ID','Roster Position','Salary','Game Info','Proj','Vol'])
print(players)
players_grp = players.groupby(["Position","ID","Proj","Salary"])
print(players_grp.head())

g1 = pg.Player('Tiger Woods',sg_true=0,sg_vol = 0.4)
g2 = pg.Player('Scottie Scheffler',sg_true=2.5, sg_vol = 0.4)
g3 = pg.Player('Brian Harman',sg_true=1.25, sg_vol = 0.5)
g4 = pg.Player('Jon Rahm',sg_true=3, sg_vol = 0.55)
g5 = pg.Player('Rory McIlroy',sg_true=2, sg_vol = 0.75)
muirfield = pg.Course('Muirfield')



memorial = pg.Tourney(player_list = [g1,g2,g3,g4,g5], course=muirfield, name='Memorial')
tiger = memorial.player_list[0]

h1 = pg.Hole(par=4)
h2 = pg.Hole(par=4)
h3 = pg.Hole(par=4)
h4 = pg.Hole(par=4)
h5 = pg.Hole(par=4)
h6 = pg.Hole(par=4)
h7 = pg.Hole(par=4)
h8 = pg.Hole(par=4)
h9 = pg.Hole(par=4)
h10 = pg.Hole(par=4)
h11 = pg.Hole(par=4)
h12 = pg.Hole(par=4)
h13 = pg.Hole(par=4)
h14 = pg.Hole(par=4)
h15 = pg.Hole(par=4)
h16 = pg.Hole(par=4)
h17 = pg.Hole(par=4)
h18 = pg.Hole(par=4)

holes = [h1,h2,h3,h4,h5,h6,h7,h8,h9,h10,h11,h12,h13,h14,h15,h16,h17,h18]

muirfield = pg.Course(holes)
print(muirfield.par)

#print(muirfield.avg_to_par)
print(muirfield.holes)



    Position                     Name + ID               Name        ID  \
0          G           Jon Rahm (27979131)           Jon Rahm  27979131   
1          G  Scottie Scheffler (27979132)  Scottie Scheffler  27979132   
2          G       Rory McIlroy (27979133)       Rory McIlroy  27979133   
3          G    Collin Morikawa (27979134)    Collin Morikawa  27979134   
4          G      Brooks Koepka (27979135)      Brooks Koepka  27979135   
..       ...                           ...                ...       ...   
154        G       Jeremy Wells (27979281)       Jeremy Wells  27979281   
155        G  Wyatt Worthington (27979282)  Wyatt Worthington  27979282   
156        G       Steven Alker (27979283)       Steven Alker  27979283   
157        G          John Daly (27979284)          John Daly  27979284   
158        G      Shaun Micheel (27979285)      Shaun Micheel  27979285   

    Roster Position  Salary         Game Info    Proj  Vol  
0                 G   11400  PGA Champ

In [18]:
wb = openpyxl.Workbook()
ws = wb.active
availables = players.groupby(["Position","ID","Name + ID","Proj","Salary"]).agg('count')#from groupby object back to reg dataframe. Prob more important for football/bball than golf with flex positions
availables = availables.reset_index()
availables.to_csv('availables.csv')
salaries = {}
points = {}
for pos in availables.Position.unique():
    availables_pos = availables[availables.Position==pos]#filtered dataframe
    salary = list(availables_pos[['Name + ID','Salary']].set_index("Name + ID").to_dict().values())[0]
    point = list(availables_pos[['Name + ID','Proj']].set_index("Name + ID").to_dict().values())[0]
    salaries[pos] = salary
    points[pos] = point
pos_num_available = {
    "G": 6
}
salary_cap = 50000



In [19]:
total_score = 1000#some number bigger than what the optimal score is
breakpoint = 0
_vars = {k: LpVariable.dict(k,v,cat='Binary') for k, v in points.items()}#simply converting values in dict to lpVariable 
prob = LpProblem("Fantasy", LpMaximize)
rewards = []
costs = []
position_constraints = []


for k, v in _vars.items():
    costs += lpSum([salaries[k][i] * _vars[k][i] for i in v])
    rewards += lpSum([points[k][i] * _vars[k][i] for i in v])
    prob += lpSum([_vars[k][i] for i in v]) == pos_num_available[k]

prob += lpSum(rewards)
prob += lpSum(costs) <= salary_cap



In [21]:

N=300
for lineup in range(1,N+1):
    breakpoint +=1
    print('breakpoint= ' + str(breakpoint))
    prob.solve()
    score = str(prob.objective)# score: 67.23*1.0 + 57.11*0.0 + 64.87*0.0 + 55.74*0.0 +
    print('score before replace: ' + score)
    constraints = [str(const) for const in prob.constraints.values()]##constraints: ['G_Aaron_Wise_(27979195) + G_Abraham_Ancer_
    colnum = 1
    for v in prob.variables():
        score = score.replace(v.name, str(v.varValue))#Replace 'Aaron Wise' with '0'
        if v.varValue !=0:
            var_name = v.name
            var_name = var_name[1+var_name.find('_'):].replace('_',' ')
            print(var_name)
            ws.cell(row=lineup, column = colnum).value = var_name
            colnum += 1
    print('score after replace: ' + score)
    total_score = eval(score)
    ws.cell(row=lineup, column=colnum).value = total_score
    print(lineup, total_score)
    prob += (lpSum(rewards) <= total_score-0.001)


wb.save('lineups.xlsx')
test = 2
print('test')





breakpoint= 151
Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/matthewmoore/.local/share/virtualenvs/optimizer_v1-vT5i3nNP/lib/python3.11/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/1q/3wk2pn_x6rdgn29l0fs4j47r0000gn/T/b064dfe0983d45d09258afff798b0340-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/1q/3wk2pn_x6rdgn29l0fs4j47r0000gn/T/b064dfe0983d45d09258afff798b0340-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 157 COLUMNS
At line 22236 RHS
At line 22389 BOUNDS
At line 22549 ENDATA
Problem MODEL has 152 rows, 159 columns and 21618 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 545.759 - 0.00 seconds
Cgl0004I processed model has 3 rows, 146 columns (146 integer (143 of which binary)) and 434 elements
Cutoff increment increased from 1e-05 to 0.00999
Cbc0038I Initial state - 3 integers u

In [ ]:
#print(prob)
#prob.solve()
#print(str(prob.objective))
print(prob.variables())

var_list = prob.variables()
print(var_list)
wise = var_list[0]
print(wise)
print(wise.varValue)

for v in prob.variables():
    print(v.name)
    print(v.varValue)


In [ ]:
test = 'G_Yannik_Paul_(27979208)'
print(test)

#test = test.replace('G_','')
print(test)

print(test.find('_'))

print(test[1+test.find('_'):])

In [ ]:
import pydkgolf as pdkg
import pandas as pd

emiliano = pdkg.Player(name='Emiliano Grillo')
emiliano.index

0